# Example 2 Darcy interface flow evaluation

In [1]:
import sys
sys.path.append("../")
from libs import *
device = torch.device('cuda:1' if torch.cuda.is_available() else 'cpu')

Package not found.


# Fourier

In [2]:
# subsample_nodes = 3
# subsample_attn = 6
# train_path = os.path.join(DATA_PATH, 'piececonst_r421_N1024_smooth1.mat')
# test_path = os.path.join(DATA_PATH, 'piececonst_r421_N1024_smooth2.mat')
# train_dataset = DarcyDataset(data_path=train_path,
#                                 subsample_attn=subsample_attn,
#                                 subsample_nodes=subsample_nodes,
#                                 train_data=True,
#                                 train_len=1024,)

# valid_dataset = DarcyDataset(data_path=test_path,
#                                 normalizer_x=train_dataset.normalizer_x,
#                                 subsample_attn=subsample_attn,
#                                 subsample_nodes=subsample_nodes,
#                                 train_data=False,
#                                 valid_len=100)
# valid_loader = DataLoader(valid_dataset, batch_size=2, shuffle=False,
#                             drop_last=False, pin_memory=True)

In [3]:
# n_grid = int(((421 - 1)/subsample_nodes) + 1)
# n_grid_c = int(((421 - 1)/subsample_attn) + 1)
# h = 1/n_grid
# metric_func = WeightedL2Loss2d(regularizer=False, h=h)
# model = torch.load(os.path.join(MODEL_PATH, 'darcy_141_6ft_256d_qkv_32f_2023-11-20.pt'))
# model.to(device)
# model.eval()
# val_metric = validate_epoch_darcy(model, metric_func, valid_loader, device)
# print(f"\nModel's validation metric: {val_metric}")

# Galerkin

In [4]:
# subsample_nodes = 3
# subsample_attn = 6
# train_path = os.path.join(DATA_PATH, 'piececonst_r421_N1024_smooth1.mat')
# test_path = os.path.join(DATA_PATH, 'piececonst_r421_N1024_smooth2.mat')
# train_dataset = DarcyDataset(data_path=train_path,
#                                 subsample_attn=subsample_attn,
#                                 subsample_nodes=subsample_nodes,
#                                 train_data=True,
#                                 train_len=1024,)

# valid_dataset = DarcyDataset(data_path=test_path,
#                                 normalizer_x=train_dataset.normalizer_x,
#                                 subsample_attn=subsample_attn,
#                                 subsample_nodes=subsample_nodes,
#                                 train_data=False,
#                                 valid_len=100)
# valid_loader = DataLoader(valid_dataset, batch_size=2, shuffle=False,
#                             drop_last=False, pin_memory=True)

In [5]:
# n_grid = int(((421 - 1)/subsample_nodes) + 1)
# n_grid_c = int(((421 - 1)/subsample_attn) + 1)
# h = 1/n_grid
# metric_func = WeightedL2Loss2d(regularizer=False, h=h)
# model = torch.load(os.path.join(MODEL_PATH, 'darcy_141_6gt_256d_qkv_32f_2023-11-20.pt'))
# model.to(device)
# model.eval()
# val_metric = validate_epoch_darcy(model, metric_func, valid_loader, device)
# print(f"\nModel's validation metric: {val_metric}")

# Lrk

In [6]:
subsample_nodes = 3
subsample_attn = 6
train_path = os.path.join(DATA_PATH, 'piececonst_r421_N1024_smooth1.mat')
test_path = os.path.join(DATA_PATH, 'piececonst_r421_N1024_smooth2.mat')
train_dataset = DarcyDataset(data_path=train_path,
                                subsample_attn=subsample_attn,
                                subsample_nodes=subsample_nodes,
                                train_data=True,
                                train_len=1,)

valid_dataset = DarcyDataset(data_path=test_path,
                                normalizer_x=train_dataset.normalizer_x,
                                subsample_attn=subsample_attn,
                                subsample_nodes=subsample_nodes,
                                train_data=False,
                                valid_len=100)
valid_loader = DataLoader(valid_dataset, batch_size=2, shuffle=False,
                            drop_last=False, pin_memory=True)

n_grid = int(((421 - 1)/subsample_nodes) + 1)
n_grid_c = int(((421 - 1)/subsample_attn) + 1)
downsample, upsample = DarcyDataset.get_scaler_sizes(n_grid, n_grid_c)


Loading piececonst_r421_N1024_smooth1.mat: start at 1743321313.27;
LOCAL RAM USAGE AT START: 0.37 GB
Loading piececonst_r421_N1024_smooth1.mat: done at 1743321364.29 (51.015649 secs elapsed);
LOCAL RAM USAGE AT END: 1.89GB (+1.52GB)


Loading piececonst_r421_N1024_smooth2.mat: start at 1743321369.64;
LOCAL RAM USAGE AT START: 2.35 GB
Loading piececonst_r421_N1024_smooth2.mat: done at 1743321417.40 (47.765023 secs elapsed);
LOCAL RAM USAGE AT END: 3.86GB (+1.51GB)




In [ ]:
h = 1/n_grid
metric_func = WeightedL2Loss2d(regularizer=False, h=h)
torch.cuda.empty_cache()
param= torch.load(os.path.join(MODEL_PATH, 'darcy_141_6Lt_256d_qkv_32f_2024-09-07.pt'))

k = len(param["v"])
print(k)

with open(os.path.join(SRC_ROOT, 'config.yml')) as f:
    config = yaml.full_load(f)['ex2_darcy']
    
config['normalizer'] = train_dataset.normalizer_y.to(device)
config['downscaler_size'] = downsample
config['upscaler_size'] = upsample
config['attn_norm'] = True

config['attention_type'] = 'Lrk'
config["k"] = k
config["seq_len"] = 5041
torch.cuda.empty_cache()
model = FourierTransformer2D(**config)
model = model.to(device)
model.load_state_dict(param)
model.eval()
print(get_num_params(model))

val_metric = validate_epoch_darcy(model, metric_func, valid_loader, device)
print(f"\nModel's validation metric: {val_metric}")

10

Model's validation metric: {'metric': 0.010892030531540513}


In [11]:
def showcontour(z, save_path=None, show_colorbar=True, **kwargs):
    '''
    show 2D solution z of its contour
    '''
    uplot = go.Contour(z=z,
                       colorscale='RdYlBu',
                       line_smoothing=0.85,
                       line_width=0.1,
                       contours=dict(
                           coloring='heatmap',
                            #   showlabels=True,
                       ),
                       showscale=show_colorbar,
                       colorbar=dict(tickformat=".0e")
                       )
    fig = go.Figure(data=uplot,
                    layout={'xaxis': {'title': 'x-label',
                                      'visible': False,
                                      'showticklabels': False},
                            'yaxis': {'title': 'y-label',
                                      'visible': False,
                                      'showticklabels': False}},)
    # fig.update_traces(showscale=False)
    if 'template' not in kwargs.keys():
        fig.update_layout(template='plotly_dark',
                        #   margin=dict(l=0, r=0, t=0, b=0),
                        margin=dict(l=0, r=50 if show_colorbar else 0, t=0, b=0),  # 右边给 colorbar 预留空间
                        # width=600+ (100 if show_colorbar else 0),  # 右边额外扩展 100px 用于 colorbar
                        # height=600,
                        **kwargs)
    else:
        fig.update_layout(margin=dict(l=0, r=0, t=0, b=0),
                          **kwargs)
    fig.show()
    if save_path:
        save_full_path = f"{save_path}.pdf"
        fig.write_image(save_full_path, format="pdf")
        print(f"The figure have been saved: {save_path}")
        
    return fig

In [12]:
sample = next(iter(valid_loader))
a = sample['node']
pos = sample['pos']
u = sample['target']
grid = sample['grid']
with torch.no_grad():
    model.eval()
    out_ = model(a.to(device), None, pos.to(device), grid.to(device))
    preds = out_['preds']

In [13]:
i = 0
z = preds[i, ..., 0].cpu().numpy()
z_true = u[i, ..., 0].cpu().numpy()
# print(z.shape)
_ = showcontour(z, save_path="darcy_pred", show_colorbar=False, width=300, height=300,)
_ = showcontour(z_true,save_path="darcy_true", show_colorbar=False, width=300, height=300,)
_ = showcontour(z_true-z, save_path = "darcy_error" ,width=400, height=300,)
print("Relative error: ", np.linalg.norm(z-z_true)/np.linalg.norm(z_true), '\n\n')

The figure have been saved: darcy_pred


The figure have been saved: darcy_true


The figure have been saved: darcy_error
Relative error:  0.01920439 




In [14]:
i = 1
z = preds[i, ..., 0].cpu().numpy()
z_true = u[i, ..., 0].cpu().numpy()
_ = showcontour(z,show_colorbar=False, width=300, height=300,)
_ = showcontour(z_true, show_colorbar=False, width=300, height=300,)
_ = showcontour(z_true-z, width=400, height=300,)
print("Relative error: ", np.linalg.norm(z-z_true)/np.linalg.norm(z_true), '\n\n')

Relative error:  0.00554581 


